In [ ]:
import json

with open('/kaggle/input/datano/diagnox.json' , 'r') as file:
    json_data = json.load(file)

In [ ]:
import pandas as p

data = p.DataFrame(json_data)
data

In [ ]:
data = data[(data['label'] == 'diagnosis') & (~data['code'].isin(['title', 'Regex']))]
data

In [ ]:
from sklearn.model_selection import train_test_split

x_train, x_test, y_train, y_test = train_test_split(data[['label', 'description']], data.code, test_size=0.3, random_state=42)
print(x_train.ndim , x_test.ndim , y_train.ndim , y_test.ndim)
print(x_train.shape , x_test.shape , y_train.shape , y_test.shape)

In [ ]:
from sklearn.preprocessing import OneHotEncoder

encoder = OneHotEncoder()

x_train_encoded = encoder.fit_transform(x_train).astype('float32')
y_train_encoded = encoder.fit_transform(y_train.values.reshape(-1 , 1)).astype('float32').toarray()

x_test_encoded = encoder.fit_transform(x_test).astype('float32')
y_test_encoded = encoder.fit_transform(y_test.values.reshape(-1 , 1)).astype('float32').toarray()
#
print(x_train_encoded.ndim , x_test_encoded.ndim , y_train_encoded.ndim , y_test_encoded.ndim)
print(x_train_encoded.shape , x_test_encoded.shape , y_train_encoded.shape , y_test_encoded.shape)

In [ ]:
from tensorflow.keras.layers import Dense
from tensorflow.keras import Sequential

model = Sequential(
    [
        Dense(16 , input_dim=x_train_encoded.shape[1] , activation = 'relu'),
        Dense(32 , activation = 'relu') , 
        Dense(64 , activation = 'relu') , 
        Dense(128 , activation = 'relu') , 
        Dense(256, activation = 'relu') , 
        Dense(32 , activation = 'relu') , 
        Dense(512 , activation = 'relu') , 
        Dense(y_train_encoded.shape[1] , activation = 'softmax')
              
    ]
)

model.summary()

In [ ]:
from tensorflow.keras.optimizers import Adam

# Compile the model with a smaller learning rate and categorical crossentropy loss
model.compile(
    optimizer=Adam(learning_rate=0.0001),  # Reduced learning rate
    loss='categorical_crossentropy',  # For multi-class classification
    metrics=['accuracy']
)

In [ ]:
model.fit(
    x_train_encoded , 
    y_train_encoded , 
    epochs = 20 , 
    batch_size = 64
)

In [ ]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
import json
# Load and prepare data
with open('/kaggle/input/datano/diagnox.json', 'r') as file:
    data = json.load(file)

In [ ]:
# Convert to DataFrame
df = pd.DataFrame(data)
df

In [ ]:
# TF-IDF Vectorization
vectorizer = TfidfVectorizer()
X = vectorizer.fit_transform(df['description'])
y = df['code']

print(X)
print(y)

In [ ]:
# Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
print(X_train.shape , X_test.shape  ,y_train.shape , y_test.shape)

In [ ]:

# Logistic Regression model
model = LogisticRegression()
model.fit(X_train, y_train)


In [ ]:
import numpy as np
from tensorflow.keras.preprocessing.text import Tokenizer  # Import from TensorFlow's Keras
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Bidirectional, Dense, Dropout, GlobalMaxPooling1D
from tensorflow.keras.optimizers import Adam
import pickle
import pandas as pd

# Load the dataset for mapping predictions to labels
data = pd.read_json('/kaggle/input/datano/diagnox.json')

# Define the max_length (must match training max_length)
max_length = 200

# Function to predict the code and label for new descriptions with confidence score
def predict_description_with_confidence(description, model, tokenizer, label_encoder):
    # Tokenize and pad the description
    sequence = tokenizer.texts_to_sequences([description])
    padded_sequence = pad_sequences(sequence, padding='post', maxlen=max_length)
    
    # Make the prediction
    prediction = model.predict(padded_sequence)
    predicted_code = np.argmax(prediction, axis=1)[0]
    confidence_score = prediction[0][predicted_code]
    
    # Map the code to the label
    predicted_code_str = label_encoder.inverse_transform([predicted_code])[0]
    predicted_label = data[data['code'] == predicted_code_str].iloc[0]['label']
    
    return {
        "description": description,
        "code": predicted_code_str,
        "label": predicted_label,
        "confidence": f"{confidence_score * 100:.2f}%"
    }

# Load tokenizer and label encoder
with open('/kaggle/input/model1/tokenizer.pkl', 'rb') as f:
    loaded_tokenizer = pickle.load(f)

with open('/kaggle/input/model1/label_encoder.pkl', 'rb') as f:
    loaded_label_encoder = pickle.load(f)

# Rebuild the model architecture
vocab_size = 5000
embedding_dim = 100
output_dim = len(loaded_label_encoder.classes_)

model = Sequential([
    Embedding(input_dim=vocab_size, output_dim=embedding_dim, input_length=max_length, trainable=False),
    Bidirectional(LSTM(128, return_sequences=True)),
    GlobalMaxPooling1D(),
    Dense(128, activation='relu'),
    Dropout(0.5),
    Dense(output_dim, activation='softmax')
])

# Compile the model
optimizer = Adam(learning_rate=0.001)
model.compile(optimizer=optimizer, loss='sparse_categorical_crossentropy', metrics=['accuracy'])

# Load the saved weights
model.load_weights('/kaggle/input/model1/diagnosis_model_advanced.h5')

# Example input description for prediction
new_description = "Type Diabetes Mellitus 1 complicated by "

# Make a prediction with confidence score
output = predict_description_with_confidence(new_description, model, loaded_tokenizer, loaded_label_encoder)

# Display the prediction with confidence score
print(output)


In [ ]:
!pip install keras 

In [ ]:
import numpy as np
import pandas as pd
import re
import os
import pickle
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
import spacy
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.layers import Embedding, LSTM, Dense, Dropout, Bidirectional, GlobalMaxPooling1D
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import RandomizedSearchCV

# Load the spaCy model for English
nlp = spacy.load('en_core_web_sm')

# Text Cleaning Function using spaCy
def clean_text(text):
    # Remove non-alphabetic characters
    text = re.sub(r'[^a-zA-Z\s]', '', text, re.I)
    # Create a spaCy document object
    doc = nlp(text.lower())
    # Lemmatize and remove stop words
    words = [token.lemma_ for token in doc if not token.is_stop and not token.is_punct]
    return ' '.join(words)

# Load dataset
data = pd.read_json('/kaggle/input/datano/diagnox.json')

# Prepare inputs (X) and labels (y)
X = data['description'].values
y = data['code'].values

# Clean the text data
X_cleaned = [clean_text(desc) for desc in X]

# Encode labels to integers
label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)

# Tokenize text and limit vocabulary size
max_vocab_size = 5000
tokenizer = Tokenizer(num_words=max_vocab_size)
tokenizer.fit_on_texts(X_cleaned)
X_tokenized = tokenizer.texts_to_sequences(X_cleaned)

# Padding sequences to fixed length
max_length = 200
X_padded = pad_sequences(X_tokenized, maxlen=max_length, padding='post')

# Split data into training and test sets
X_train, X_test, y_train, y_test = train_test_split(X_padded, y_encoded, test_size=0.2, random_state=42)

# Load pre-trained word vectors (GloVe)
embedding_dim = 100  # You can choose 50, 100, 200, 300
embedding_index = {}
glove_file = f'glove.6B.{embedding_dim}d.txt'
with open(os.path.join('/kaggle/input/glove1/glove.6B', glove_file), encoding='utf-8') as f:
    for line in f:
        values = line.split()
        word = values[0]
        coefs = np.asarray(values[1:], dtype='float32')
        embedding_index[word] = coefs

# Prepare embedding matrix
embedding_matrix = np.zeros((max_vocab_size, embedding_dim))
for word, i in tokenizer.word_index.items():
    if i < max_vocab_size:
        embedding_vector = embedding_index.get(word)
        if embedding_vector is not None:
            embedding_matrix[i] = embedding_vector

# Define the model
def build_model(optimizer='adam', lstm_units=128, dropout_rate=0.5):
    model = Sequential([
        Embedding(input_dim=max_vocab_size, output_dim=embedding_dim, input_length=max_length, weights=[embedding_matrix], trainable=False),
        Bidirectional(LSTM(lstm_units, return_sequences=True)),  # Bidirectional LSTM
        GlobalMaxPooling1D(),
        Dense(128, activation='relu'),
        Dropout(dropout_rate),
        Dense(64, activation='relu'),  # Additional Dense Layer
        Dropout(dropout_rate),
        Dense(len(label_encoder.classes_), activation='softmax')  # Output layer
    ])
    
    model.compile(optimizer=optimizer, loss='sparse_categorical_crossentropy', metrics=['accuracy'])
    return model

# Hyperparameter tuning with RandomizedSearchCV
# Instead of using KerasClassifier, we directly pass the model-building function to RandomizedSearchCV

def model_fn(optimizer='adam', lstm_units=128, dropout_rate=0.5):
    model = build_model(optimizer, lstm_units, dropout_rate)
    return model

param_grid = {
    'optimizer': ['adam', 'rmsprop'],
    'lstm_units': [64, 128, 256],
    'dropout_rate': [0.3, 0.5, 0.7]
}
model = model_fn()  

# Now pass the model instance to RandomizedSearchCV
random_search = RandomizedSearchCV(estimator=model, param_distributions=param_grid, n_iter=5, cv=3)
random_search.fit(X_train, y_train)
# Get the best hyperparameters
print("Best Hyperparameters:", random_search.best_params_)

# Use the best model
best_model = random_search.best_estimator_

# Early stopping and learning rate reduction
early_stopping = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)
lr_scheduler = ReduceLROnPlateau(monitor='val_loss', factor=0.2, patience=2, min_lr=0.0001)

# Train the model
history = best_model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=100, batch_size=32, 
                         callbacks=[early_stopping, lr_scheduler])

# Evaluate the model
loss, accuracy = best_model.evaluate(X_test, y_test)
print(f"Test Accuracy: {accuracy * 100:.2f}%")

# Save the model and tokenizer
best_model.save('diagnosis_model_advanced.h5')
with open('tokenizer.pkl', 'wb') as f:
    pickle.dump(tokenizer, f)
with open('label_encoder.pkl', 'wb') as f:
    pickle.dump(label_encoder, f)

# Plot the training and validation accuracy
plt.plot(history.history['accuracy'], label='Training Accuracy')
plt.plot(history.history['val_accuracy'], label='Validation Accuracy')
plt.title('Training and Validation Accuracy')
plt.xlabel('Epochs')
plt.ylabel('Accuracy')
plt.legend()
plt.show()

# Plot the training and validation loss
plt.plot(history.history['loss'], label='Training Loss')
plt.plot(history.history['val_loss'], label='Validation Loss')
plt.title('Training and Validation Loss')
plt.xlabel('Epochs')
plt.ylabel('Loss')
plt.legend()
plt.show()

# Function to predict the code and label for new descriptions with confidence score
def predict_description_with_confidence(description, model, tokenizer, label_encoder):
    sequence = tokenizer.texts_to_sequences([description])
    padded_sequence = pad_sequences(sequence, padding='post', maxlen=max_length)
    prediction = model.predict(padded_sequence)
    predicted_code = np.argmax(prediction, axis=1)[0]
    confidence_score = prediction[0][predicted_code]
    predicted_code_str = label_encoder.inverse_transform([predicted_code])[0]
    predicted_label = data[data['code'] == predicted_code_str].iloc[0]['label']
    
    return {
        "description": description,
        "code": predicted_code_str,
        "label": predicted_label,
        "confidence": f"{confidence_score * 100:.2f}%"
    }

# Example input description for prediction
new_description = "Secondary carcinoid tumors of bone"

# Load the trained model and tokenizer for prediction
loaded_model = load_model('diagnosis_model_advanced.h5')
with open('tokenizer.pkl', 'rb') as f:
    loaded_tokenizer = pickle.load(f)
with open('label_encoder.pkl', 'rb') as f:
    loaded_label_encoder = pickle.load(f)

# Make a prediction with confidence score
output = predict_description_with_confidence(new_description, loaded_model, loaded_tokenizer, loaded_label_encoder)
print(output)


In [ ]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense, Dropout, Bidirectional, GlobalMaxPooling1D, Conv1D, MaxPooling1D  , Input
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.optimizers import Adam
from tensorflow.keras import Model
from tensorflow.keras import regularizers
import json
import os
import pickle

# Load dataset
data = pd.read_json('/kaggle/input/datano/diagnox.json')

# Prepare inputs (X) and labels (y)
X = data['description'].values
y = data['code'].values

# Encode labels to integers
label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)

# Tokenize text and limit vocabulary size
max_vocab_size = 5000
tokenizer = Tokenizer(num_words=max_vocab_size)
tokenizer.fit_on_texts(X)
X_tokenized = tokenizer.texts_to_sequences(X)

max_length = 200
X_padded = pad_sequences(X_tokenized, maxlen=max_length, padding='post')

X_train, X_test, y_train, y_test = train_test_split(X_padded, y_encoded, test_size=0.2, random_state=42)

# Load pre-trained word vectors (e.g., GloVe)
embedding_dim = 300  # Increased embedding dimension for more parameters
embedding_index = {}
glove_file = f'glove.6B.{embedding_dim}d.txt'
with open(os.path.join('/kaggle/input/glove1/glove.6B', glove_file), encoding='utf-8') as f:
    for line in f:
        values = line.split()
        word = values[0]
        coefs = np.asarray(values[1:], dtype='float32')
        embedding_index[word] = coefs

# Prepare embedding matrix
embedding_matrix = np.zeros((max_vocab_size, embedding_dim))
for word, i in tokenizer.word_index.items():
    if i < max_vocab_size:
        embedding_vector = embedding_index.get(word)
        if embedding_vector is not None:
            embedding_matrix[i] = embedding_vector

# Define the model
vocab_size = max_vocab_size
output_dim = len(label_encoder.classes_)


# Increased model size with larger LSTM layers, Dense layers, and Conv1D
input_layer = Input(shape=(max_length,))
embedding_layer = Embedding(input_dim=max_vocab_size, output_dim=embedding_dim, input_length=max_length)(input_layer)

# Increase the units and layers to scale the parameters
conv_layer = Conv1D(2048, 5, activation='relu')(embedding_layer)
maxpool_layer = MaxPooling1D(pool_size=4)(conv_layer)

# Increased number of LSTM units
lstm_layer = Bidirectional(LSTM(8192, return_sequences=True))(maxpool_layer)  # LSTM with 8192 units

global_max_pool = GlobalMaxPooling1D()(lstm_layer)
dense_layer = Dense(8192, activation='relu')(global_max_pool)  # Dense with 8192 units
dropout_layer = Dropout(0.6)(dense_layer)

# Final output layer with softmax activation for classification
output_layer = Dense(len(label_encoder.classes_), activation='softmax')(dropout_layer)

# Compile the model
model = Model(inputs=input_layer, outputs=output_layer)

optimizer = Adam(learning_rate=0.001)
model.compile(optimizer=optimizer, loss='sparse_categorical_crossentropy', metrics=['accuracy'])

model.summary()
    

In [ ]:
import pandas as pd
import re
import nltk
from nltk.corpus import stopwords
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.multioutput import MultiOutputClassifier
from sklearn.pipeline import make_pipeline
from sklearn.metrics import classification_report

# Ensure NLTK stopwords are downloaded
nltk.download('stopwords')

# Text cleaning function
def clean_text(text):
    text = text.lower()
    text = re.sub(r'[^a-z\s]', '', text)
    stop_words = set(stopwords.words('english'))
    words = text.split()
    words = [word for word in words if word not in stop_words]
    return ' '.join(words)

# Example dataset
data = pd.read_json('/kaggle/input/datano/diagnox.json')
# Apply text cleaning to descriptions
data['description'] = data['description'].apply(clean_text)

# Prepare training data
descriptions = data['description'].tolist()
labels = data['label'].tolist()
codes = data['code'].tolist()

# Split dataset into train and test
X_train, X_test, y_train_labels, y_test_labels = train_test_split(descriptions, labels, test_size=0.2, random_state=42)
_, _, y_train_codes, y_test_codes = train_test_split(descriptions, codes, test_size=0.2, random_state=42)

# Combine labels and codes into a single target variable for multi-output classification
y_train = list(zip(y_train_labels, y_train_codes))
y_test = list(zip(y_test_labels, y_test_codes))

# Create a model pipeline: TF-IDF + MultiOutput Logistic Regression
vectorizer = TfidfVectorizer()
model = make_pipeline(vectorizer, MultiOutputClassifier(LogisticRegression(max_iter=1000)))

# Train the model
model.fit(X_train, y_train)

# Evaluate the model on the test data
y_pred = model.predict(X_test)
print(classification_report(y_test, y_pred))

# Testing the trained model on some example unstructured data
unstructured_data = "patient has Diabetes and disorder"
unstructured_data_clean = clean_text(unstructured_data)
predicted_label, predicted_code = model.predict([unstructured_data_clean])[0]
print(f"Predicted Label: {predicted_label}, Predicted Code: {predicted_code}")


In [ ]:
import json
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from tensorflow.keras.models import load_model
from tensorflow.keras.initializers import Orthogonal
from tensorflow.keras.preprocessing.sequence import pad_sequences
import pickle

# Define custom objects
custom_objects = {
    'Orthogonal': Orthogonal
}

# Load your model with custom objects
try:
    loaded_model = load_model('/kaggle/input/model1/diagnosis_model_advanced.h5', custom_objects=custom_objects)
    print("Model loaded successfully!")
except Exception as e:
    print("Error loading model:", e)

# Load tokenizer and label encoder
try:
    with open('/kaggle/input/final-model/tokenizer.pkl', 'rb') as f:
        loaded_tokenizer = pickle.load(f)
    with open('/kaggle/input/final-model/label_encoder.pkl', 'rb') as f:
        loaded_label_encoder = pickle.load(f)
    print("Tokenizer and label encoder loaded successfully!")
except Exception as e:
    print("Error loading tokenizer/label encoder:", e)

# Load the JSON data (descriptions)
try:
    with open('/kaggle/input/datano/diagnox.json', 'r') as f:
        descriptions_data = json.load(f)
    print("Descriptions data loaded successfully!")
except Exception as e:
    print("Error loading descriptions data:", e)

# Extract the descriptions from the JSON data for comparison
descriptions = [item['description'] for item in descriptions_data]

def find_best_matching_description(unstructured_text, descriptions):
    # Use bigrams in the vectorizer for better semantic capture
    vectorizer = TfidfVectorizer(ngram_range=(1, 2), stop_words='english', max_features=5000)
    all_texts = [unstructured_text] + descriptions
    tfidf_matrix = vectorizer.fit_transform(all_texts)
    cosine_similarities = cosine_similarity(tfidf_matrix[0:1], tfidf_matrix[1:]).flatten()

    # Print cosine similarities to debug
    print("Cosine Similarities:", cosine_similarities)

    most_similar_index = np.argmax(cosine_similarities)
    return descriptions[most_similar_index], descriptions_data[most_similar_index]

def predict_description_with_confidence(description, model, tokenizer, label_encoder, max_length=100):
    sequence = tokenizer.texts_to_sequences([description])
    padded_sequence = pad_sequences(sequence, padding='post', maxlen=max_length)
    prediction = model.predict(padded_sequence)
    predicted_code = np.argmax(prediction, axis=1)[0]
    confidence_score = prediction[0][predicted_code]
    predicted_code_str = label_encoder.inverse_transform([predicted_code])[0]
    predicted_label = next(item['label'] for item in descriptions_data if item['code'] == predicted_code_str)
    return {
        "description": description,
        "code": predicted_code_str,
        "label": predicted_label,
        "confidence": f"{confidence_score * 100:.2f}%"
    }

def predict_from_unstructured_text(unstructured_text, model, tokenizer, label_encoder, descriptions_data):
    best_match_description, best_match_metadata = find_best_matching_description(unstructured_text, descriptions)
    result = predict_description_with_confidence(best_match_description, model, tokenizer, label_encoder)
    return result

#  Example unstructured text
unstructured_text = """
   patient states her symptoms are lymph node swelling and tongue swelling that started in september.
"""

# Make the prediction
try:
    output = predict_from_unstructured_text(unstructured_text, loaded_model, loaded_tokenizer, loaded_label_encoder, descriptions_data)
    print("Prediction:", output)
except Exception as e:
    print("Error during prediction:", e)


print("Unstructured Text:\n", unstructured_text)
print("\nFirst 5 Descriptions:\n", descriptions[:5])

print("Tokenized Unstructured Text:", loaded_tokenizer.texts_to_sequences([unstructured_text]))



In [ ]:
from transformers import BertTokenizer, BertModel
import torch

# Load pre-trained BERT tokenizer and model
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained('bert-base-uncased')

def get_bert_embeddings(text):
    inputs = tokenizer(text, return_tensors='pt', padding=True, truncation=True, max_length=512)
    with torch.no_grad():
        outputs = model(**inputs)
    # We take the embeddings from the last hidden state
    embeddings = outputs.last_hidden_state.mean(dim=1).squeeze().numpy()
    return embeddings

# Get embeddings for unstructured text and descriptions
unstructured_text_embedding = get_bert_embeddings(unstructured_text)
descriptions_embeddings = [get_bert_embeddings(desc) for desc in descriptions]

# Calculate cosine similarity between unstructured text and descriptions embeddings
from sklearn.metrics.pairwise import cosine_similarity
cosine_similarities = cosine_similarity([unstructured_text_embedding], descriptions_embeddings).flatten()

# Find the best match based on cosine similarity
most_similar_index = np.argmax(cosine_similarities)
best_match_description = descriptions[most_similar_index]
print(f"Best matching description: {best_match_description}")


In [ ]:
import pandas as pd


data = pd.read_json('/kaggle/input/datano/diagnox.json')

print(data.head())

In [ ]:
y = data.description[18816 : ]
x = data['description'][ : 43904]

print(y)

In [ ]:
# Step 3: Ensure x and y have the same length
if len(x) != len(y):
    print("Warning: x and y have different lengths! Adjusting...")
    # Adjusting y to match x's length by slicing (you can also truncate x or y as needed)
    min_len = min(len(x), len(y))
    x = x[:min_len]
    y = y[:min_len]

In [ ]:
from sklearn.model_selection import train_test_split
# Step 4: Split into train and test sets (optional but recommended)
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=42)

print(x_train.ndim , x_test.ndim , y_train.ndim , y_test.shape)

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
# Reduce the number of features for TF-IDF
tfidf_vectorizer = TfidfVectorizer(stop_words='english', max_features=1000)

x_train_tfidf = tfidf_vectorizer.fit_transform(x_train)
x_test_tfidf = tfidf_vectorizer.transform(x_test)

In [ ]:
from sklearn.linear_model import LogisticRegression


# Use a more appropriate solver for large data or sparse data
model = LogisticRegression(max_iter=1000, solver='liblinear')

# Train the model
model.fit(x_train_tfidf, y_train)

In [ ]:
input = """
patient name patricia stith date birth 08281947 dysphagia oropharyngeal phase ph 8593401377 past medical history condition answer notes heart attack mi cancer colon hypertension history present illness note 76yo tongue swelling given cephalexin 91423 completed given chlorhexidine mouth wash doxycycline methylprednisone triamcinolone paste thursday started wanted wait see ent said patient states symptoms lymph node swelling tongue swelling started september caused problems talking swallowing unable wear dentures states seen er told couldnt determine cause released former smoker stopped smoking 2016 history colon cancer colectomy husband states past couple months black blood stool odorous since stopped without review systems brief otolaryngology ros reported patient constitutional sweats weight gain unintended weight loss intolerance eyes eyes eyes change ears hearing pain pressure discharge nose nosebleeds congestion pressure obstruction enmt nasal drip mouththroat throat gums mouth abnormalities ulcers abnormalities breathing taste tonsils change difficulty swallowing cardiovascular pain pain exertion breath cardiovascular walking breath lying breath awakens sleep heart murmur extremity swelling respiratory breath rest shortness breath exertion apnea production gastrointestinal pain normal appetite black tarry stools stools swelling neurologic consciousness dizziness headaches disturbances legs normal gait psychiatric psych difficulties concentrating hematologiclymphatic glands bruising hematologiclymphatic problems allergyimmunologic nose pressure allergicimmunologic physical exam ent exam general appearance healthyappearing wellnourished well groomed distress constitutional communication normal communication wo aids normal voice quality inspection atraumatic facial strength normal strength normal symmetry tic sinuses salivary headface glands parotid glands masses submandibular glands masses inspection tmj symmetric opening motion palpation tmj nontender eyes pupils eom intact perrla conjunctiva noninjected right hearing rinne acbc weber midline left hearing rinne acbc weber midline right external ear normally formed free lesions left external ear normally formed free lesions right external auditory canal normal appearance erythema left external auditory canal normal appearance right tympanic membrane mobile pneumatic otoscopy pearly grey landmarks clear left tympanic membrane mobile pneumatic otoscopy pearly grey landmarks clear nasal skin nasal dorsum symmetric palpable deformities nasal tip normal symmetric nasal tip normal nasal valves nasal page 7 8
"""
input = [[input]]

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

# Example input data (your provided input)
input_text = """
patient name patricia stith date birth 08281947 dysphagia oropharyngeal phase ph 8593401377 ...
"""

# Create a TF-IDF vectorizer instance
vectorizer = TfidfVectorizer()

# Convert the input data into a numerical format (vector)
input_vectorized = vectorizer.fit_transform([input_text])

# Now input_vectorized is in numerical format and can be passed into the model
y_pred = model.predict(input_vectorized)


In [ ]:
print(y_pred)

In [ ]:
model.score(x_test_tfidf , y_test *100)

print(model.score(x_train_tfidf , y_train *100))

In [ ]:
import json
import pdfplumber
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression

def extract_text_from_pdf(pdf_path):
    with pdfplumber.open(pdf_path) as pdf:
        return " ".join([page.extract_text() for page in pdf.pages])

def match_and_predict(text, data, model=None, vectorizer=None):
    # Match with JSON data
    text_lower = text.lower()
    matches = [entry for entry in data if text_lower in entry["description"].lower()]

    if matches:
        return matches
    elif model and vectorizer:
        # Predict using ML model
        vectorized_text = vectorizer.transform([text])
        prediction = model.predict(vectorized_text)
        return [{"code": None, "label": "predicted", "description": prediction[0]}]
    else:
        return []

# Load data and train model
def train_model(data):
    descriptions = [entry['description'] for entry in data]
    labels = [entry['code'] for entry in data]
    vectorizer = TfidfVectorizer()
    X = vectorizer.fit_transform(descriptions)
    model = LogisticRegression()
    model.fit(X, labels)
    return model, vectorizer

# Main workflow
pdf_path = "/kaggle/input/pdf-data/401152946.pdf"
data_file_path = "/kaggle/input/datano/diagnox.json"
with open(data_file_path, 'r') as file:
    data = json.load(file)

# Train model
model, vectorizer = train_model(data)

# Analyze PDF
report_text = extract_text_from_pdf(pdf_path)
results = match_and_predict(report_text, data, model, vectorizer)

# Display results
for result in results:
    print(f"Code: {result['code']}, Label: {result['label']}, Description: {result['description']}")


In [ ]:
import spacy

# Load the spaCy model
nlp = spacy.load("en_core_web_sm")

# Function to process the text and clean it
def process_text(text):
    # Process the text using spaCy
    doc = nlp(text)
    
    # Remove stopwords, punctuation, and apply lemmatization
    cleaned_tokens = []
    for token in doc:
        # Remove stopwords and punctuation, and lemmatize
        if not token.is_stop and not token.is_punct:
            # Ensure the lemma is a string and add it to the list
            lemma = str(token.lemma_)  # Use token.lemma_ which is always a string
            cleaned_tokens.append(lemma)  # Add lemmatized token as a string
    
    # Join the cleaned tokens back into a single string
    return " ".join(cleaned_tokens)

# Read text from the file
with open('/kaggle/input/text-1/demotxt.txt', 'r') as file:
    text = file.read()

# Process the text
cleaned_text = process_text(text)

# Save the cleaned text to another file
with open('cleaned_output.txt', 'w') as file:
    file.write(cleaned_text)

# Optionally print cleaned text
print("Original Text: \n", text[:])  # Print first 500 characters of original text
print("\nCleaned Text: \n", cleaned_text[:500])  # Print first 500 characters of cleaned text


In [ ]:
import spacy

# Load the spaCy model
nlp = spacy.load("en_core_web_sm")

# Function to process the text and clean it with more detailed steps
def process_text(text):
    # Process the text using spaCy
    doc = nlp(text)
    
    # Remove stopwords, punctuation, non-alphabetic tokens, and apply lemmatization
    cleaned_tokens = []
    for token in doc:
        # Remove stopwords, punctuation, and non-alphabetic tokens
        if not token.is_stop and not token.is_punct and token.is_alpha:
            # Ensure the lemma is a string and add it to the list
            lemma = str(token.lemma_)  # Use token.lemma_ which is always a string
            cleaned_tokens.append(lemma)  # Add lemmatized token as a string
    
    # Join the cleaned tokens back into a single string
    cleaned_text = " ".join(cleaned_tokens)
    
    # Remove any leading or trailing whitespaces
    cleaned_text = cleaned_text.strip()
    
    return cleaned_text

# Read text from the file
with open('/kaggle/input/text-1/demotxt.txt', 'r') as file:
    text = file.read()

# Process the text
cleaned_text = process_text(text)

# Save the cleaned text to another file
with open('cleaned_output.txt', 'w') as file:
    file.write(cleaned_text)

# Optionally print cleaned text (first 500 characters)
print("\nCleaned Text: \n", cleaned_text[:])  # Print first 500 characters of cleaned text


In [ ]:
import re

def clean_clinical_data(text):
    # Step 1: Remove addresses (general street and location patterns)
    text = re.sub(r'\d{1,5}\s[A-Za-z\s]+(?:Street|Road|Drive|Ave|Boulevard|St|Suite|Lane|Court)', '', text)

    # Step 2: Remove phone numbers (formats like (123) 456-7890, 123-456-7890, etc.)
    text = re.sub(r'\(?\d{3}\)?[\s.-]?\d{3}[\s.-]?\d{4}', '', text)

    # Step 3: Remove specific phrases like "hospital lab registration" and other location-based phrases
    text = re.sub(r'\b(?:hospital lab registration|bourbon community|linville dr paris|lexington rd georgetown ky)\b', '', text)

    # Step 4: Remove metadata-like content such as document, file, record, etc.
    text = re.sub(r'\b(?:document|file|record|referral|registration|note|procedure)\b[^\n]*\n', '', text)

    # Step 5: Remove personal info like names, DOB, SSN, etc.
    # Regex to remove patient information such as name, DOB, SSN, and other personal identifiers
    text = re.sub(r'\b(?:patient|contact|social security number|phone|dob|name|address)\b[^\n]*\n?', '', text, flags=re.DOTALL)

    # Step 6: Clean extra spaces, multiple spaces, and newlines
    text = re.sub(r'\s+', ' ', text).strip()

    return text

# Sample raw text (abbreviated version for debugging)
raw_text = """
patient patricia stith date birth coordinator healthplans encounter summary patricia stith electronically sign leslie asbury md social security number xxx encounter oid service event encounter participant leslie ann asbury contact linville drive suite e paris ky ph legal authenticator leslie asbury md electronically sign contact lexington rd georgetown ky ph table content reason visit chief complaint assessment plan treatment medication medication administer vital sign result problem procedure 
"""

# Apply the cleaning function to the raw text
cleaned_text = clean_clinical_data(raw_text)

# Print the cleaned text (first 500 characters)
print("Final Cleaned Text Preview (First 500 chars):")
print(cleaned_text[:500])  # This should print the first 500 characters of cleaned text


In [ ]:
import nltk
import re
import string
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import TruncatedSVD
from gensim.models import Word2Vec
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize

# Download NLTK data (if not already downloaded)
nltk.download('punkt')
nltk.download('stopwords')


In [ ]:
import pandas as pd
import numpy as np
import re
import os
import pickle
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential, load_model 
from tensorflow.keras.layers import Embedding, LSTM, Dense, Dropout, Bidirectional, GlobalMaxPooling1D , SimpleRNN
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.optimizers import Adam

# Check if GPU is available
physical_devices = tf.config.list_physical_devices('GPU')
if physical_devices:
    print(f'{len(physical_devices)} GPU(s) available: {physical_devices}')
    for device in physical_devices:
        tf.config.experimental.set_memory_growth(device, True)
else:
    print('No GPU available, using CPU.')

# Load dataset
data = pd.read_json('/kaggle/input/datano/diagnox.json')

# Preprocess the text to ensure it is a string
def preprocess_text(text):
    text = str(text)  # Convert to string
    text = text.lower()  # Convert text to lowercase
    text = re.sub(r'\d+', '', text)  # Remove numbers
    text = re.sub(r'[^\w\s]', '', text)  # Remove punctuation
    return text

# Apply preprocessing to the descriptions
data['description'] = data['description'].apply(preprocess_text)

# Prepare inputs (X) and labels (y)
X = data['description'].values
y = data['code'].values

# Encode labels to integers
label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)

# Tokenize text and limit vocabulary size
max_vocab_size = 5000
tokenizer = Tokenizer(num_words=max_vocab_size)
tokenizer.fit_on_texts(X)
X_tokenized = tokenizer.texts_to_sequences(X)
max_length = 200
X_padded = pad_sequences(X_tokenized, maxlen=max_length, padding='post')
X_train, X_test, y_train, y_test = train_test_split(X_padded, y_encoded, test_size=0.2, random_state=42)

# Load pre-trained word vectors (e.g., GloVe)
embedding_dim = 100  # You can choose 50, 100, 200, 300
embedding_index = {}
glove_file = f'glove.6B.{embedding_dim}d.txt'
with open(os.path.join('/kaggle/input/glove1/glove.6B', glove_file), encoding='utf-8') as f:
    for line in f:
        values = line.split()
        word = values[0]
        coefs = np.asarray(values[1:], dtype='float32')
        embedding_index[word] = coefs

# Prepare embedding matrix
embedding_matrix = np.zeros((max_vocab_size, embedding_dim))
for word, i in tokenizer.word_index.items():
    if i < max_vocab_size:
        embedding_vector = embedding_index.get(word)
        if embedding_vector is not None:
            embedding_matrix[i] = embedding_vector

# Use distributed strategy
strategy = tf.distribute.MirroredStrategy()

with strategy.scope():
    vocab_size = max_vocab_size
    output_dim = len(label_encoder.classes_)
    model = Sequential([
        Embedding(input_dim=vocab_size, output_dim=embedding_dim, input_shape=(max_length,), weights=[embedding_matrix], trainable=False),
        Bidirectional(SimpleRNN(512, return_sequences=True)),
        GlobalMaxPooling1D(),
        Dense(128, activation='relu'),
        Dropout(0.5),
        Dense(output_dim, activation='softmax')
    ])
    optimizer = Adam(learning_rate=0.001)
    model.compile(optimizer=optimizer, loss='sparse_categorical_crossentropy', metrics=['accuracy'])

# Print the model summary
model.summary()

early_stopping = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)
history = model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=100, batch_size=16, callbacks=[early_stopping])

loss, accuracy = model.evaluate(X_test, y_test)
print(f"Test Accuracy: {accuracy * 100:.2f}%")

model.save('diagnosis_model_advanced.h5')
with open('tokenizer.pkl', 'wb') as f:
    pickle.dump(tokenizer, f)
with open('label_encoder.pkl', 'wb') as f:
    pickle.dump(label_encoder, f)

# Function to predict the code and label for new descriptions with confidence score
def predict_description_with_confidence(description, model, tokenizer, label_encoder):
    # Tokenize and pad the description
    sequence = tokenizer.texts_to_sequences([description])
    padded_sequence = pad_sequences(sequence, padding='post', maxlen=max_length)
    # Make the prediction
    prediction = model.predict(padded_sequence)
    predicted_code = np.argmax(prediction, axis=1)[0]
    confidence_score = prediction[0][predicted_code]
    # Map the code to the label
    predicted_code_str = label_encoder.inverse_transform([predicted_code])[0]
    predicted_label = data[data['code'] == predicted_code_str].iloc[0]['label']
    return {
        "description": description,
        "code": predicted_code_str,
        "label": predicted_label,
        "confidence": f"{confidence_score * 100:.2f}"
    }

# Example input description for prediction
new_description = "Secondary carcinoid tumors of bone"

# Load the trained model and tokenizer
loaded_model = load_model('diagnosis_model_advanced.h5')
with open('tokenizer.pkl', 'rb') as f:
    loaded_tokenizer = pickle.load(f)
with open('label_encoder.pkl', 'rb') as f:
    loaded_label_encoder = pickle.load(f)

# Make a prediction with confidence score
output = predict_description_with_confidence(new_description, loaded_model, loaded_tokenizer, loaded_label_encoder)

# Display the prediction with confidence score
print(output)


In [ ]:
import jeeva
import requests
from bs4 import BeautifulSoup
from googlesearch import search
import spacy

# Initialize spaCy
nlp = spacy.load("en_core_web_sm")

# Perform a Google search
query = "Python programming"
for url in search(query, num_results=5):
    print(f"Found URL: {url}")

    # Fetch the URL content
    response = requests.get(url)
    soup = BeautifulSoup(response.content, "html.parser")

    # Extract text from the webpage
    text = soup.get_text()

    # Use spaCy to analyze the text
    doc = nlp(text)
    for sent in doc.sents:
        print(sent.text)


In [ ]:
import pandas as pd
import json
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder


with open('/kaggle/input/datano/diagnox.json') as f:
    data = json.load(f)

df = pd.DataFrame(data)


df['combined_label'] = df['label'] + '-' + df['code']


df['description'] = df['description'].str.lower()


label_encoder = LabelEncoder()
df['encoded_label'] = label_encoder.fit_transform(df['combined_label'])


X_train, X_test, y_train, y_test = train_test_split(df['description'], df['encoded_label'], test_size=0.2, random_state=42)


print(X_train.shape , X_test.shape , y_train.shape , y_test.shape)

print(X_train.ndim , X_test.ndim , y_train.ndim , y_test.ndim)

In [ ]:
from transformers import BertTokenizer, BertForSequenceClassification
from transformers import Trainer, TrainingArguments
import torch
from torch.utils.data import Dataset
from sklearn.metrics import accuracy_score


tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')


class CustomDataset(Dataset):
    def __init__(self, descriptions, labels, tokenizer, max_length):
        self.descriptions = descriptions
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.descriptions)

    def __getitem__(self, idx):
        text = self.descriptions.iloc[idx]
        label = self.labels.iloc[idx]

        encoding = self.tokenizer.encode_plus(
            text,
            add_special_tokens=True,
            max_length=self.max_length,
            padding='max_length',
            truncation=True,
            return_tensors='pt'
        )

        return {
            'input_ids': encoding['input_ids'].flatten(),
            'attention_mask': encoding['attention_mask'].flatten(),
            'labels': torch.tensor(label, dtype=torch.long)
        }


MAX_LENGTH = 128
BATCH_SIZE = 16


train_dataset = CustomDataset(X_train, y_train, tokenizer, MAX_LENGTH)
test_dataset = CustomDataset(X_test, y_test, tokenizer, MAX_LENGTH)


model = BertForSequenceClassification.from_pretrained('bert-base-uncased', num_labels=len(df['combined_label'].unique()))


def compute_metrics(p):
    predictions, labels = p
    predictions = torch.tensor(predictions) if not isinstance(predictions, torch.Tensor) else predictions
    labels = torch.tensor(labels) if not isinstance(labels, torch.Tensor) else labels
    
    # Get the index of the highest logit (predicted class)
    predictions = torch.argmax(predictions, dim=-1)
    
    # Calculate accuracy
    return {"eval_accuracy": accuracy_score(labels.cpu().numpy(), predictions.cpu().numpy())}


# Training arguments
training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=3,
    per_device_train_batch_size=BATCH_SIZE,
    per_device_eval_batch_size=BATCH_SIZE,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    metric_for_best_model="eval_accuracy", 
)


trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics  
)


trainer.train()


eval_result = trainer.evaluate()
print(f"Test Accuracy: {eval_result['eval_accuracy']:.2f}")

In [ ]:
def predict_description(description):
    # Ensure the model is on the correct device (CPU or GPU)
    device = model.device  # Check the device where the model is located
    
    encoding = tokenizer.encode_plus(
        description,
        add_special_tokens=True,
        max_length=MAX_LENGTH,
        padding='max_length',
        truncation=True,
        return_tensors='pt'
    ).to(device)  # Move the input tensors to the same device as the model
    
    # Forward pass through the model
    output = model(**encoding)
    
    # Get the predicted label id
    predicted_label_id = output.logits.argmax(dim=1).item()
    
    # Decode the predicted label id back to the label string
    predicted_label = label_encoder.inverse_transform([predicted_label_id])
    return predicted_label[0]

# Example usage:
new_description =   "Acute coccidioidomycosis"
predicted_label = predict_description(new_description)
print(f"Predicted Label-Code: {predicted_label}")


In [ ]:
import pandas as pd
import json
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
import torch
from transformers import BertTokenizer, BertForSequenceClassification, Trainer, TrainingArguments
from transformers import EarlyStoppingCallback
from torch.utils.data import Dataset
from sklearn.metrics import accuracy_score

# Load data
with open('/kaggle/input/datano/diagnox.json') as f:
    data = json.load(f)

df = pd.DataFrame(data)

# Combine label and code for unique class identification
df['combined_label'] = df['label'] + '-' + df['code']

# Preprocess descriptions
df['description'] = df['description'].str.lower()

# Label encode combined label
label_encoder = LabelEncoder()
df['encoded_label'] = label_encoder.fit_transform(df['combined_label'])

# Train-test split
X_train, X_test, y_train, y_test = train_test_split(df['description'], df['encoded_label'], test_size=0.2, random_state=42)

# Check the shapes of the data
print(X_train.shape, X_test.shape, y_train.shape, y_test.shape)

# Tokenizer and Dataset class
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

# Create Dataset class
class CustomDataset(Dataset):
    def __init__(self, descriptions, labels, tokenizer, max_length, device):
        self.descriptions = descriptions
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_length = max_length
        self.device = device

    def __len__(self):
        return len(self.descriptions)

    def __getitem__(self, idx):
        text = self.descriptions.iloc[idx]
        label = self.labels.iloc[idx]

        encoding = self.tokenizer.encode_plus(
            text,
            add_special_tokens=True,
            max_length=self.max_length,
            padding='max_length',
            truncation=True,
            return_tensors='pt'
        )
        
        # Move tensors to the correct device (GPU or CPU)
        input_ids = encoding['input_ids'].flatten().to(self.device)
        attention_mask = encoding['attention_mask'].flatten().to(self.device)
        label_tensor = torch.tensor(label, dtype=torch.long).to(self.device)
        
        return {
            'input_ids': input_ids,
            'attention_mask': attention_mask,
            'labels': label_tensor
        }

# Define constants
MAX_LENGTH = 256  # Increased max length
BATCH_SIZE = 32  # Larger batch size for potentially better results

# Set device to GPU if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Create datasets
train_dataset = CustomDataset(X_train, y_train, tokenizer, MAX_LENGTH, device)
test_dataset = CustomDataset(X_test, y_test, tokenizer, MAX_LENGTH, device)

# Load pre-trained BERT model and move it to GPU
model = BertForSequenceClassification.from_pretrained('bert-base-uncased', num_labels=len(df['combined_label'].unique()))
model.to(device)

# Compute metrics function
def compute_metrics(p):
    predictions, labels = p

    # Ensure that predictions and labels are both PyTorch tensors on the same device
    predictions = torch.tensor(predictions).to(device) if not isinstance(predictions, torch.Tensor) else predictions.to(device)
    labels = torch.tensor(labels).to(device) if not isinstance(labels, torch.Tensor) else labels.to(device)

    # Get the index of the highest logit (predicted class)
    predictions = torch.argmax(predictions, dim=-1)

    # Calculate accuracy
    return {"eval_accuracy": accuracy_score(labels.cpu().numpy(), predictions.cpu().numpy())}

# Training arguments with tuned hyperparameters
training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=5,
    per_device_train_batch_size=BATCH_SIZE,
    per_device_eval_batch_size=BATCH_SIZE,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    metric_for_best_model="eval_accuracy", 
    learning_rate=2e-5,  # Learning rate tuned
)

# Initialize the Trainer with EarlyStoppingCallback
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics,
    callbacks=[EarlyStoppingCallback(early_stopping_patience=2)]  # Early stopping callback
)

# Train the model
trainer.train()

# Evaluate the model
eval_result = trainer.evaluate()
print(f"Test Accuracy: {eval_result['eval_accuracy']:.2f}")


In [ ]:

from transformers import AutoTokenizer, AutoModelForTokenClassification
import torch

# Load the tokenizer and model for medical NER (Named Entity Recognition)
tokenizer = AutoTokenizer.from_pretrained("AdaptLLM/medicine-LLM")
model = AutoModelForTokenClassification.from_pretrained("AdaptLLM/medicine-LLM")

# Sample unstructured medical text
text = """
patient name: patricia stith i date of birth: 08/28/1947 nose: mucosa: normal, pink and moist. septum: not markedly deformed. 
turbinates: normal size and confrontation. polyps: none lips, teeth, gums: normal lips, normal gums, normal dentition. 
oral mucosa: normal, moist, . palate: normal hard palate, normal soft palate. tongue: normal tongue, lesions, . tonsils: normal tonsils, . 
posterior pharynx: normal. cavity/mouth: hypopharynx: normal hypopharynx, normal tongue base, normal pyriform sinus. larynx: normal epiglottis, 
normal false vocal cords, normal true vocal cords, normal glottic mobility. nasopharynx: normal, normal adenoids, normal eustachian tubes, choanae patent 
neck: symmetrical, trachea midline. thyroid: symmetric, , , neck:  inspection/auscultation: good air movement, chest expands symmetrically, clear bilaterally, 
respiratory: normal breath sounds, , /crackles, ,  cardiovascular auscultation: regular rate and rhythm, , , . observation/palpation of peripheral vascular system: , 
carotid pulse normal, system:  cervical:  lymph node enlargement,  adenopathy,  lymph nodes: cervical adenopathy,  cervical adenopathy,  adenopathy. axillary:  
lymph node enlargement orientation: oriented to time, oriented to place, oriented to person. mood and affect: normal mood, normal affect. cranial nerves: cranial nerves 
ii-xii intact. cerebellar: neurological negative romberg's sign, normal finger-nose pointing, normal gait. vestibulocular: : nystagmus,  induced from horizontal head 
shaking test, normal evaluation of positional nystagmus advance directives unknown. functional status unknown.  screening assessment done in the clinical encounter 
mental status unknown.  screening assessment done in the clinical encounter demographics sex: female ethnicity: not hispanic or latino dob: 08/28/1947 race: white 
preferred language: en marital status: married contact: 722 steele ford road, paris, ky 40361, us, ph. tel:+1-859-7072481 document information document identifier 
document created 11902eea-9754-11ef-86a2-e974acb157af 10/31/2024, 02:52 document maintained by athenahealth contact boston landing, 80 guest street, boston, 
ma 02135, us, ph. el:+1-617-4021000 care team members primary care provider leslie n asbury md 8 linville dr, ste e, paris, ky 40361, us, ph. tel:+1-859-3401377 page 8 of 8
"""

# Tokenize the input text
inputs = tokenizer(text, return_tensors="pt", truncation=True, padding=True, max_length=512)

# Get predictions from the model
with torch.no_grad():
    outputs = model(**inputs).logits

# Get predicted labels
predictions = torch.argmax(outputs, dim=2)

# Decode token labels back to words
tokens = tokenizer.convert_ids_to_tokens(inputs['input_ids'][0])

# Display the medical terms (entities) based on the predicted labels
label_map = model.config.id2label
entities = []

for token, prediction in zip(tokens, predictions[0].tolist()):
    if label_map[prediction] != 'O':  # 'O' means no entity detected
        entities.append((token, label_map[prediction]))

# Print out the entities
print("Extracted Medical Terms and their Labels:")
for entity in entities:
    print(f"Term: {entity[0]}, Label: {entity[1]}")


In [ ]:
import pandas as pd
import numpy as np
import tensorflow as tf
from transformers import BertTokenizer, TFBertForSequenceClassification
from sklearn.model_selection import train_test_split

# Load your dataset
data = pd.read_json('/kaggle/input/datano/diagnox.json')
df = pd.DataFrame(data)

# Tokenization
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
X = list(df['description'])
y = list(df['code'])

# Encode the labels
label_map = {label: i for i, label in enumerate(set(y))}
y = np.array([label_map[label] for label in y])

# Tokenize the input texts
X_tokenized = tokenizer(X, padding=True, truncation=True, return_tensors='tf')

# Convert tokenized data to numpy arrays
input_ids = np.array(X_tokenized['input_ids'])
attention_mask = np.array(X_tokenized['attention_mask'])

# Split the dataset, including attention masks
X_train_ids, X_test_ids, y_train, y_test = train_test_split(input_ids, y, test_size=0.2, random_state=42)
X_train_mask, X_test_mask = train_test_split(attention_mask, test_size=0.2, random_state=42)

# Convert to TensorFlow datasets
train_dataset = tf.data.Dataset.from_tensor_slices(({'input_ids': X_train_ids, 'attention_mask': X_train_mask}, y_train))
test_dataset = tf.data.Dataset.from_tensor_slices(({'input_ids': X_test_ids, 'attention_mask': X_test_mask}, y_test))

# Enable GPU if available
if tf.config.list_physical_devices('GPU'):
    print("GPU is available and will be used for training.")
    strategy = tf.distribute.MirroredStrategy()
else:
    print("GPU is not available, using CPU.")
    strategy = tf.distribute.OneDeviceStrategy(device="/cpu:0")

# Build and compile the model within strategy scope
with strategy.scope():
    model = TFBertForSequenceClassification.from_pretrained('bert-base-uncased', num_labels=len(label_map))
    model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=2e-5),
                  loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
                  metrics=['accuracy'])

# Train the model
model.fit(train_dataset.shuffle(1000).batch(16),
          epochs=3,
          batch_size=16)

# Evaluate the model
model.evaluate(test_dataset.batch(16))

# Save the model
model.save_pretrained('./model')

# For prediction on new text
def predict(text):
    inputs = tokenizer(text, return_tensors='tf', padding=True, truncation=True)
    outputs = model(inputs['input_ids'])
    predictions = tf.nn.softmax(outputs.logits, axis=-1)
    predicted_label = tf.argmax(predictions, axis=1).numpy()
    for label, idx in label_map.items():
        if idx == predicted_label:
            return label

# Example usage
new_text = "patient name: patricia stith i date of birth: 08/28/1947 ..."
predicted_label = predict(new_text)
print(f"Predicted Label: {predicted_label}")


In [ ]:
def predict(text):
    inputs = tokenizer(text, return_tensors='tf', padding=True, truncation=True)
    outputs = model(inputs['input_ids'])
    predictions = tf.nn.softmax(outputs.logits, axis=-1)
    predicted_label = tf.argmax(predictions, axis=1).numpy()
    for label, idx in label_map.items():
        if idx == predicted_label:
            return label

# Example usage
new_text = """
"text": "patient name: patricia stith i date of birth: 08/28/1947 nose: mucosa: normal, pink and moist. septum: not markedly deformed. turbinates: normal size and confrontation. polyps: none lips, teeth, gums: normal lips, normal gums, normal dentition. oral mucosa: normal, moist, . palate: normal hard palate, normal soft palate. tongue: normal tongue,  lesions, . tonsils: normal tonsils, . posterior pharynx: normal. cavity/mouth: hypopharynx: normal hypopharynx, normal tongue base, normal pyriform sinus. larynx: normal epiglottis, normal false vocal cords, normal true vocal cords, normal glottic mobility. nasopharynx: normal, normal adenoids, normal eustachian tubes, choanae patent neck: symmetrical, trachea midline. thyroid: symmetric, , , neck:  inspection/auscultation: good air movement, chest expands symmetrically, clear bilaterally, respiratory: normal breath sounds, , /crackles, ,  cardiovascular auscultation: regular rate and rhythm, , , . observation/palpation of peripheral vascular system: , carotid pulse normal, system:  cervical:  lymph node enlargement,  adenopathy,  lymph nodes: cervical adenopathy,  cervical adenopathy,  adenopathy. axillary:  lymph node enlargement orientation: oriented to time, oriented to place, oriented to person. mood and affect: normal mood, normal affect. cranial nerves: cranial nerves ii-xii intact. cerebellar: neurological negative romberg's sign, normal finger-nose pointing, normal gait. vestibulocular: : nystagmus,  induced from horizontal head shaking test, normal evaluation of positional nystagmus advance directives unknown. functional status unknown.  screening assessment done in the clinical encounter mental status unknown.  screening assessment done in the clinical encounter demographics sex: female ethnicity: not hispanic or latino dob: 08/28/1947 race: white preferred language: en marital status: married contact: 722 steele ford road, paris, ky 40361, us, ph. tel:+1-859-7072481 document information document identifier document created 11902eea-9754-11ef-86a2-e974acb157af 10/31/2024, 02:52 document maintained by athenahealth contact boston landing, 80 guest street, boston, ma 02135, us, ph. el:+1-617-4021000 care team members primary care provider leslie n asbury md 8 linville dr, ste e, paris, ky 40361, us, ph. tel:+1-859-3401377 page 8 of 8",
"""
predicted_label = predict(new_text)
print(f"Predicted Label: {predicted_label}")

In [ ]:
import torch
import os
from transformers import BertTokenizer, BertForSequenceClassification, Trainer, TrainingArguments
from datasets import Dataset
from sklearn.model_selection import train_test_split
import pandas as pd
from sklearn.preprocessing import LabelEncoder

# Set PyTorch memory configuration to handle fragmentation
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"

# Load and prepare your dataset
data = pd.read_json('/kaggle/input/datano/diagnox.json')  # Update path to your JSON file
df = pd.DataFrame(data)

# Encode labels (codes)
label_encoder = LabelEncoder()
df['encoded_code'] = label_encoder.fit_transform(df['code'])

# Split data into train and test sets
train_data, test_data = train_test_split(df, test_size=0.2, random_state=42)

# Load pre-trained BERT tokenizer (choose smaller BERT model for better memory handling)
tokenizer = BertTokenizer.from_pretrained('distilbert-base-uncased')  # You can also use TinyBERT or ClinicalBERT

# Tokenize the descriptions (text) using BERT tokenizer
def tokenize_function(examples):
    return tokenizer(examples['description'], padding="max_length", truncation=True, max_length=64)  # Reduce max_length to 64

# Convert data to Dataset format and ensure the label column is correctly mapped
train_dataset = Dataset.from_pandas(train_data)
test_dataset = Dataset.from_pandas(test_data)

# Map the tokenization function to the datasets
train_dataset = train_dataset.map(tokenize_function, batched=True)
test_dataset = test_dataset.map(tokenize_function, batched=True)

# Remove any existing 'label' column and use 'encoded_code' as the label
train_dataset = train_dataset.remove_columns(['label'])  # Remove any existing 'label' column
test_dataset = test_dataset.remove_columns(['label'])  # Remove any existing 'label' column

# Rename the 'encoded_code' column to 'label'
train_dataset = train_dataset.rename_column('encoded_code', 'label')
test_dataset = test_dataset.rename_column('encoded_code', 'label')

# Load pre-trained BERT model for sequence classification (distilled BERT or ClinicalBERT)
model = BertForSequenceClassification.from_pretrained('distilbert-base-uncased', num_labels=len(label_encoder.classes_))

training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=3,
    per_device_train_batch_size=4,  # Increase batch size if memory allows
    per_device_eval_batch_size=4,
    gradient_accumulation_steps=4,
    warmup_steps=500,
    weight_decay=0.1,  # Increased weight decay for better regularization
    logging_dir='./logs',
    logging_steps=10,
    fp16=True,
    save_steps=500,
    save_total_limit=3,
    dataloader_num_workers=4,
    load_best_model_at_end=True,
    evaluation_strategy="steps",
    eval_steps=500,
    report_to="none",
    learning_rate=2e-5,  # Lower learning rate
    lr_scheduler_type='linear',  # Use a linear learning rate scheduler
)


# Initialize Trainer
trainer = Trainer(
    model=model,                         # The instantiated model
    args=training_args,                  # Training arguments
    train_dataset=train_dataset,         # Training dataset
    eval_dataset=test_dataset            # Evaluation dataset
)

# Train the model
trainer.train()

# Save the model
trainer.save_model("fine_tuned_bert_model")

# Make predictions
def predict(text):
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=64)
    with torch.no_grad():
        logits = model(**inputs).logits
    predictions = torch.argmax(logits, dim=-1)
    predicted_code = label_encoder.inverse_transform(predictions.numpy())
    return predicted_code[0]

# Example prediction
text = "Patient diagnosed with Diabetes mellitus type 2 with complications"
predicted_code = predict(text)
print(f"Predicted Code: {predicted_code}")

# Clear GPU memory after training to prevent fragmentation
torch.cuda.empty_cache()


In [ ]:
import torch

# Clear GPU memory
torch.cuda.empty_cache()


In [ ]:
!nvidia-smi

In [ ]:
import spacy
from med7 import med7

# Load Med7 model
nlp = spacy.load("en_core_med7_lg")

# Unstructured text
text = """patient name: patricia stith i date of birth: 08/28/1947 nose: mucosa: normal, pink and moist ..."""

# Process text
doc = nlp(text)

# Extract entities
for ent in doc.ents:
    print(f"{ent.text} - {ent.label_}")

In [ ]:
! pip install med7

In [ ]:


# 1. Data Preprocessing and Text Cleaning

# Function to clean and preprocess text (remove special characters and convert to lowercase)
def clean_text(text):
    # Remove non-alphanumeric characters and convert to lowercase
    text = re.sub(r'[^a-zA-Z\s]', '', text)
    text = text.lower()
    return text

# Clean the descriptions in the structured dataset
df['cleaned_description'] = df['description'].apply(clean_text)

# 2. Text Vectorization: Convert text descriptions to numerical form using TF-IDF
vectorizer = TfidfVectorizer(stop_words='english')

# Fit the vectorizer on the cleaned descriptions and transform them into numerical vectors
X = vectorizer.fit_transform(df['cleaned_description'])

# 3. Train-Test Split
# Prepare the labels for prediction (Code and Label)
y = df[['code', 'label']]

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# 4. Model: Multi-output Classifier (Logistic Regression)
# We use MultiOutputClassifier to predict multiple labels
model = MultiOutputClassifier(LogisticRegression(max_iter=1000))

# Train the model
model.fit(X_train, y_train)

# 5. Evaluate the model
y_pred = model.predict(X_test)

# Display the classification report to evaluate the model performance
print("Classification Report:")
print(classification_report(y_test, y_pred))

# 6. Make Predictions on Unstructured Text
# Define an example of unstructured text
unstructured_text = """
"patient name: patricia stith i date of birth: 08/28/1947 nose: mucosa: normal, pink and moist. septum: not markedly deformed. turbinates: normal size and confrontation. polyps: none lips, teeth, gums: normal lips, normal gums, normal dentition. oral mucosa: normal, moist, . palate: normal hard palate, normal soft palate. tongue: normal tongue,  lesions, . tonsils: normal tonsils, . posterior pharynx: normal. cavity/mouth: hypopharynx: normal hypopharynx, normal tongue base, normal pyriform sinus. larynx: normal epiglottis, normal false vocal cords, normal true vocal cords, normal glottic mobility. nasopharynx: normal, normal adenoids, normal eustachian tubes, choanae patent neck: symmetrical, trachea midline. thyroid: symmetric, , , neck:  inspection/auscultation: good air movement, chest expands symmetrically, clear bilaterally, respiratory: normal breath sounds, , /crackles, ,  cardiovascular auscultation: regular rate and rhythm, , , . observation/palpation of peripheral vascular system: , carotid pulse normal, system:  cervical:  lymph node enlargement,  adenopathy,  lymph nodes: cervical adenopathy,  cervical adenopathy,  adenopathy. axillary:  lymph node enlargement orientation: oriented to time, oriented to place, oriented to person. mood and affect: normal mood, normal affect. cranial nerves: cranial nerves ii-xii intact. cerebellar: neurological negative romberg's sign, normal finger-nose pointing, normal gait. vestibulocular: : nystagmus,  induced from horizontal head shaking test, normal evaluation of positional nystagmus advance directives unknown. functional status unknown.  screening assessment done in the clinical encounter mental status unknown.  screening assessment done in the clinical encounter demographics sex: female ethnicity: not hispanic or latino dob: 08/28/1947 race: white preferred language: en marital status: married contact: 722 steele ford road, paris, ky 40361, us, ph. tel:+1-859-7072481 document information document identifier document created 11902eea-9754-11ef-86a2-e974acb157af 10/31/2024, 02:52 document maintained by athenahealth contact boston landing, 80 guest street, boston, ma 02135, us, ph. el:+1-617-4021000 care team members primary care provider leslie n asbury md 8 linville dr, ste e, paris, ky 40361, us, ph. tel:+1-859-3401377 page 8 of 8",
"""

# Clean and vectorize the unstructured text
unstructured_text_clean = clean_text(unstructured_text)
unstructured_vector = vectorizer.transform([unstructured_text_clean])

# Make predictions on the unstructured text
predicted_code, predicted_label = model.predict(unstructured_vector)

# Display the predictions
print(f"Predicted Code: {predicted_code[0]}, Predicted Label: {predicted_label[0]}")


In [ ]:
import pandas as pd
import json
import re
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.multioutput import MultiOutputClassifier
from sklearn.metrics import classification_report

# Sample structured data (as JSON)
data = pd.read_json('/kaggle/input/datano/diagnox.json')

# Convert JSON data to DataFrame
df = pd.DataFrame(data)

print(df.head())

In [ ]:
# Function to clean and preprocess text (remove special characters and convert to lowercase)
def clean_text(text):
    # Remove non-alphanumeric characters and convert to lowercase
    text = re.sub(r'[^a-zA-Z\s]', '', text)
    text = text.lower()
    return text

In [ ]:
# Clean the descriptions in the structured dataset
df['cleaned_description'] = df['description'].apply(clean_text)

# 2. Text Vectorization: Convert text descriptions to numerical form using TF-IDF
vectorizer = TfidfVectorizer(stop_words='english')

# Fit the vectorizer on the cleaned descriptions and transform them into numerical vectors
X = vectorizer.fit_transform(df['cleaned_description'])
print(X)

# 3. Train-Test Split
# Prepare the labels for prediction (Code and Label)
y = df[['code', 'label']]

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

print(X_train.shape , X_test.shape , y_train.shape , y_test.shape)
print(X_train.ndim , X_test.ndim , y_train.ndim , y_test.ndim)

In [ ]:
model = MultiOutputClassifier(LogisticRegression(max_iter=1000))



In [ ]:
model.fit(X_train, y_train)

In [ ]:




# 5. Build a Deep Learning Model using Bidirectional LSTM
model = Sequential()

# Add embedding layer (to convert word indices to dense vectors)
model.add(Embedding(input_dim=10000, output_dim=128, input_length=100))

# Add a Bidirectional LSTM layer
model.add(Bidirectional(LSTM(units=64, return_sequences=False)))

# Add a dropout layer for regularization
model.add(Dropout(0.5))

# Add two output layers: one for the code and one for the label
model.add(Dense(64, activation='relu'))
model.add(Dense(len(code_encoder.classes_), activation='softmax', name='code_output'))  # For 'code'
model.add(Dense(len(label_encoder.classes_), activation='softmax', name='label_output'))  # For 'label'

# 6. Compile the model
model.compile(optimizer='adam', 
              loss={'code_output': 'sparse_categorical_crossentropy', 'label_output': 'sparse_categorical_crossentropy'}, 
              metrics=['accuracy'])

# 7. Train the model
model.fit(X_train, {'code_output': y_train_code, 'label_output': y_train_label}, 
          epochs=5, batch_size=32, validation_data=(X_test, {'code_output': y_test_code, 'label_output': y_test_label}))

# 8. Evaluate the model
y_pred_code, y_pred_label = model.predict(X_test)

# Convert predictions to label indices
y_pred_code = np.argmax(y_pred_code, axis=1)
y_pred_label = np.argmax(y_pred_label, axis=1)

# Display the classification report
print("Classification Report for Code:")
print(classification_report(y_test_code, y_pred_code))

print("Classification Report for Label:")
print(classification_report(y_test_label, y_pred_label))

# 9. Make Predictions on New Unstructured Text
unstructured_text = """patient name: patricia stith i date of birth: 08/28/1947 nose: mucosa: normal, pink and moist. septum: not markedly deformed. turbinates: normal size and confrontation. polyps: none lips, teeth, gums: normal lips, normal gums, normal dentition. oral mucosa: normal, moist..."""

# Clean and preprocess the unstructured text
unstructured_text_clean = clean_text(unstructured_text)
unstructured_sequence = tokenizer.texts_to_sequences([unstructured_text_clean])

# Pad the sequence to match the input length
unstructured_sequence = pad_sequences(unstructured_sequence, padding='post', maxlen=100)

# Make prediction for the unstructured text
pred_code, pred_label = model.predict(unstructured_sequence)

# Convert predicted indices back to original labels
pred_code_label = code_encoder.inverse_transform(np.argmax(pred_code, axis=1))
pred_label_label = label_encoder.inverse_transform(np.argmax(pred_label, axis=1))

print(f"Predicted Code: {pred_code_label[0]}, Predicted Label: {pred_label_label[0]}")


In [ ]:
import pandas as pd
import re
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import classification_report
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense, Dropout, Bidirectional
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

# Load and inspect the data
data = pd.read_json('/kaggle/input/datano/diagnox.json')

# Convert JSON data to DataFrame
df = pd.DataFrame(data)

# Check for missing or None values
print(df.isnull().sum())  # This will show if any column has missing values

In [ ]:
# 1. Data Preprocessing and Text Cleaning
def clean_text(text):
    if text is None:
        return ''  # If text is None, return an empty string
    text = re.sub(r'[^a-zA-Z\s]', '', text)  # Remove non-alphanumeric characters
    text = text.lower()  # Convert text to lowercase
    return text

# Fill any NaN or None descriptions with an empty string
df['description'] = df['description'].fillna('')

# Clean the descriptions
df['cleaned_description'] = df['description'].apply(clean_text)

# Check if the text is cleaned properly
print(df[['description', 'cleaned_description']].head())

In [ ]:
# 2. Tokenization and Sequence Padding
tokenizer = Tokenizer(num_words=10000)  # Using top 10000 words
tokenizer.fit_on_texts(df['cleaned_description'])

# Convert text to sequences
X = tokenizer.texts_to_sequences(df['cleaned_description'])

# Pad sequences to ensure uniform length
X = pad_sequences(X, padding='post', maxlen=100)

# Check if the sequences are padded correctly
print(X.shape)

# 3. Label Encoding for 'code' and 'label'
code_encoder = LabelEncoder()
df['encoded_code'] = code_encoder.fit_transform(df['code'])

label_encoder = LabelEncoder()
df['encoded_label'] = label_encoder.fit_transform(df['label'])

# Prepare target variables
y_code = df['encoded_code']
y_label = df['encoded_label']

# 4. Train-Test Split
X_train, X_test, y_train_code, y_test_code, y_train_label, y_test_label = train_test_split(
    X, y_code, y_label, test_size=0.2, random_state=42
)

In [ ]:
# 5. Build a Deep Learning Model using Bidirectional LSTM
model = Sequential()

# Add embedding layer (to convert word indices to dense vectors)
model.add(Embedding(input_dim=10000, output_dim=128, input_length=100))

# Add a Bidirectional LSTM layer
model.add(Bidirectional(LSTM(units=64, return_sequences=False)))

# Add a dropout layer for regularization
model.add(Dropout(0.5))

# Add two output layers: one for the code and one for the label
model.add(Dense(64, activation='relu'))
model.add(Dense(len(code_encoder.classes_), activation='softmax', name='code_output'))  # For 'code'
model.add(Dense(len(label_encoder.classes_), activation='softmax', name='label_output'))  # For 'label'

model.summary()

In [ ]:
# 6. Compile the model
model.compile(optimizer='adam', 
              loss={'code_output': 'sparse_categorical_crossentropy', 'label_output': 'sparse_categorical_crossentropy'}, 
              metrics=['accuracy'])
model.summary()

In [ ]:

# 7. Train the model
model.fit(X_train, {'code_output': y_train_code, 'label_output': y_train_label}, 
          epochs=5, batch_size=32, validation_data=(X_test, {'code_output': y_test_code, 'label_output': y_test_label}))

In [ ]:
import tensorflow as tf
try:
    tpu = tf.distribute.cluster_resolver.TPUClusterResolver()  # Will automatically detect TPU
    print("TPU detected")
except ValueError:
    print("No TPU detected")


In [ ]:
import tensorflow as tf

# Check if TPU devices are available
devices = tf.config.list_physical_devices('TPU')

if devices:
    print("TPU device found.")
    
    try:
        # Check if it's a Cloud TPU environment, otherwise skip
        tpu_resolver = tf.distribute.cluster_resolver.TPUClusterResolver('local')
        strategy = tf.distribute.TPUStrategy(tpu_resolver)
    except Exception as e:
        print("Error with TPUClusterResolver:", e)
        print("Falling back to GPU/CPU strategy.")
        strategy = tf.distribute.MirroredStrategy()  # Fallback to MirroredStrategy for GPU/CPU
else:
    print("TPU not available. Using MirroredStrategy for GPU/CPU.")
    strategy = tf.distribute.MirroredStrategy()  # Fallback to MirroredStrategy for GPU/CPU

# Continue with model definition within strategy scope
with strategy.scope():
    # Your model code here
    pass


In [ ]:
!pip install tensorflow 

In [ ]:
import pandas as pd

import re

import numpy as np

from sklearn.model_selection import train_test_split

from sklearn.preprocessing import LabelEncoder

from sklearn.metrics import classification_report

import tensorflow as tf

from tensorflow.keras.models import Sequential

from tensorflow.keras.layers import Embedding, LSTM, Dense, Dropout, Bidirectional

from tensorflow.keras.preprocessing.text import Tokenizer

from tensorflow.keras.preprocessing.sequence import pad_sequences
 
# Check for GPU

print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))
 
# Load the JSON data into a pandas DataFrame

data = pd.read_json('/kaggle/input/datano/diagnox.json')
 
# Convert JSON data to DataFrame

df = pd.DataFrame(data)
 
# Check for None or NaN values

print("Checking for None or NaN values:")

print(df.isna().sum())
 
# 1. Data Preprocessing and Text Cleaning

def clean_text(text):

    if text is None:

        return ''  # If text is None, return an empty string

    text = re.sub(r'[^a-zA-Z\s]', '', text)  # Remove non-alphanumeric characters

    text = text.lower()  # Convert text to lowercase

    return text
 
# Fill any NaN or None descriptions with an empty string

df['description'] = df['description'].fillna('')
 
# Clean the descriptions

df['cleaned_description'] = df['description'].apply(clean_text)
 
# 2. Tokenization and Sequence Padding

tokenizer = Tokenizer(num_words=10000)  # Using top 10000 words

tokenizer.fit_on_texts(df['cleaned_description'])
 
X = tokenizer.texts_to_sequences(df['cleaned_description'])

X = pad_sequences(X, padding='post', maxlen=100)
 
# 3. Label Encoding for 'code' and 'label'

code_encoder = LabelEncoder()

df['encoded_code'] = code_encoder.fit_transform(df['code'])
 
label_encoder = LabelEncoder()

df['encoded_label'] = label_encoder.fit_transform(df['label'])
 
y_code = df['encoded_code']

y_label = df['encoded_label']
 
# 4. Train-Test Split

X_train, X_test, y_train_code, y_test_code, y_train_label, y_test_label = train_test_split(

    X, y_code, y_label, test_size=0.2, random_state=42

)
 
#from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau
from tensorflow.keras.layers import LeakyReLU, BatchNormalization
from tensorflow.keras.callbacks import EarlyStopping  , ReduceLROnPlateau
from tensorflow.keras import Input
from tensorflow.keras.regularizers import l1 , l2
from tensorflow.keras import Model

early_stopping = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)
lr_scheduler = ReduceLROnPlateau(monitor='val_loss', factor=0.5, patience=3, min_lr=1e-6)

input_layer = Input(shape=(100,))
embedding_layer = Embedding(input_dim=10000, output_dim=128, input_length=100)(input_layer)
lstm_layer = Bidirectional(LSTM(units=128, return_sequences=False, kernel_regularizer=l2(0.1)))(embedding_layer)
lstm_layer = BatchNormalization()(lstm_layer)
dropout_layer = Dropout(0.5)(lstm_layer)
dense_layer = Dense(64)(dropout_layer)
dense_layer = LeakyReLU(alpha=0.3)(dense_layer)

code_output = Dense(len(code_encoder.classes_), activation='softmax', name='code_output', kernel_regularizer=l2(0.1))(dense_layer)
label_output = Dense(len(label_encoder.classes_), activation='softmax', name='label_output', kernel_regularizer=l2(0.1))(dense_layer)

model = Model(inputs=input_layer, outputs=[code_output, label_output])

model.compile(optimizer='adam', 
              loss={'code_output': 'sparse_categorical_crossentropy', 'label_output': 'sparse_categorical_crossentropy'}, 
              metrics={'code_output': 'accuracy', 'label_output': 'accuracy'})

history = model.fit(X_train, {'code_output': y_train_code, 'label_output': y_train_label},
                    epochs=1000, batch_size=32, validation_data=(X_test, {'code_output': y_test_code, 'label_output': y_test_label}),
                    callbacks=[early_stopping, lr_scheduler])

 
 
model.evaluate(X_test, {'code_output': y_test_code, 'label_output': y_test_label}, batch_size=32)

# 8. Evaluate the model

y_pred_code, y_pred_label = model.predict(X_test)

y_pred_code = np.argmax(y_pred_code, axis=1)

y_pred_label = np.argmax(y_pred_label, axis=1)
 
print("Classification Report for Code:")

print(classification_report(y_test_code, y_pred_code))

print("Classification Report for Label:")

print(classification_report(y_test_label, y_pred_label))
 
# 9. Make Predictions on New Unstructured Text

unstructured_text = """patient name: patricia stith i date of birth: 08/28/1947 nose: mucosa: normal, pink and moist. septum: not markedly deformed. turbinates: normal size and confrontation. polyps: none lips, teeth, gums: normal lips, normal gums, normal dentition. oral mucosa: normal, moist..."""
 
unstructured_text_clean = clean_text(unstructured_text)

unstructured_sequence = tokenizer.texts_to_sequences([unstructured_text_clean])

unstructured_sequence = pad_sequences(unstructured_sequence, padding='post', maxlen=100)
 
pred_code, pred_label = model.predict(unstructured_sequence)

pred_code_label = code_encoder.inverse_transform(np.argmax(pred_code, axis=1))

pred_label_label = label_encoder.inverse_transform(np.argmax(pred_label, axis=1))
 
print(f"Predicted Code: {pred_code_label[0]}")

print(f"Predicted Label: {pred_label_label[0]}")

 

In [ ]:
model.save('final_model.h5')

In [ ]:
from tensorflow.keras.models import load_model
import numpy as np

# Load the trained model
model = load_model('/kaggle/working/final_model.h5')

# Input unstructured text
unstructured_text = "Idiopathic aseptic necrosis of"

# Clean the input text (ensure `clean_text` function is defined)
unstructured_text_clean = clean_text(unstructured_text)

# Convert the cleaned text to sequences using the tokenizer
unstructured_sequence = tokenizer.texts_to_sequences([unstructured_text_clean])

# Pad the sequences
unstructured_sequence = pad_sequences(unstructured_sequence, padding='post', maxlen=100)

# Predict the code and label using the model
pred_code, pred_label = model.predict(unstructured_sequence)

# Get the predicted code and label
pred_code_label = code_encoder.inverse_transform(np.argmax(pred_code, axis=1))
pred_label_label = label_encoder.inverse_transform(np.argmax(pred_label, axis=1))

# Get the confidence for the predicted code and label (probability of the predicted class)
pred_code_confidence = np.max(pred_code)
pred_label_confidence = np.max(pred_label)

# Print the predictions along with their confidence
print(f"Predicted Code: {pred_code_label[0]} with confidence {pred_code_confidence:.4f}")
print(f"Predicted Label: {pred_label_label[0]} with confidence {pred_label_confidence:.4f}")


In [ ]:
import pandas as pd
import re
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import classification_report
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Embedding, LSTM, Dense, Dropout, Bidirectional, Input, LeakyReLU, BatchNormalization
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau
from tensorflow.keras.regularizers import l2

# Detect and connect to TPU (only in environments that support TPU like Colab)
try:
    tpu = tf.distribute.cluster_resolver.TPUClusterResolver()  # Initialize TPU
    tf.tpu.experimental.initialize_tpu_system(tpu)  # Initialize TPU system
    tpu_strategy = tf.distribute.TPUStrategy(tpu)  # Create TPU strategy
    print("Running on TPU")
except ValueError:
    # Fall back to GPU or CPU if TPU is not available
    tpu_strategy = tf.distribute.get_strategy()
    print("Running on GPU/CPU")

# Load JSON data into a pandas DataFrame
data = pd.read_json('/kaggle/input/datano/diagnox.json')
df = pd.DataFrame(data)

# Data Preprocessing
def clean_text(text):
    if text is None:
        return ''  # If text is None, return an empty string
    text = re.sub(r'[^a-zA-Z\s]', '', text)  # Remove non-alphanumeric characters
    text = text.lower()  # Convert text to lowercase
    return text

df['description'] = df['description'].fillna('')
df['cleaned_description'] = df['description'].apply(clean_text)

# Tokenization and Sequence Padding
tokenizer = Tokenizer(num_words=10000)  # Top 10,000 words
tokenizer.fit_on_texts(df['cleaned_description'])

X = tokenizer.texts_to_sequences(df['cleaned_description'])
X = pad_sequences(X, padding='post', maxlen=100)

# Label Encoding
code_encoder = LabelEncoder()
df['encoded_code'] = code_encoder.fit_transform(df['code'])

label_encoder = LabelEncoder()
df['encoded_label'] = label_encoder.fit_transform(df['label'])

y_code = df['encoded_code']
y_label = df['encoded_label']

# Train-Test Split
X_train, X_test, y_train_code, y_test_code, y_train_label, y_test_label = train_test_split(
    X, y_code, y_label, test_size=0.2, random_state=42
)

# Define callbacks
early_stopping = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)
lr_scheduler = ReduceLROnPlateau(monitor='val_loss', factor=0.5, patience=3, min_lr=1e-6)

# Check if TPU devices are available
devices = tf.config.list_physical_devices('TPU')

if devices:
    print("TPU device found.")
    
    try:
        # Set up TPU strategy for distributed training
        tpu_resolver = tf.distribute.cluster_resolver.TPUClusterResolver('local')
        strategy = tf.distribute.TPUStrategy(tpu_resolver)
    except Exception as e:
        print("Error with TPUClusterResolver:", e)
        print("Falling back to GPU/CPU strategy.")
        strategy = tf.distribute.MirroredStrategy()  # Fallback to MirroredStrategy for GPU/CPU
else:
    print("TPU not available. Using MirroredStrategy for GPU/CPU.")
    strategy = tf.distribute.MirroredStrategy()  # Fallback to MirroredStrategy for GPU/CPU


# Define the model architecture within the TPU strategy scope
with tpu_strategy.scope():  # Define model within TPU strategy scope
    input_layer = Input(shape=(100,))
    embedding_layer = Embedding(input_dim=10000, output_dim=128, input_length=100)(input_layer)
    lstm_layer = Bidirectional(LSTM(units=128, return_sequences=False, kernel_regularizer=l2(0.01)))(embedding_layer)
    lstm_layer = BatchNormalization()(lstm_layer)
    dropout_layer = Dropout(0.5)(lstm_layer)
    dense_layer = Dense(64)(dropout_layer)
    dense_layer = LeakyReLU(alpha=0.3)(dense_layer)

    code_output = Dense(len(code_encoder.classes_), activation='softmax', name='code_output', kernel_regularizer=l2(0.01))(dense_layer)
    label_output = Dense(len(label_encoder.classes_), activation='softmax', name='label_output', kernel_regularizer=l2(0.01))(dense_layer)

    model = Model(inputs=input_layer, outputs=[code_output, label_output])

    model.compile(
        optimizer='adam', 
        loss={'code_output': 'sparse_categorical_crossentropy', 'label_output': 'sparse_categorical_crossentropy'}, 
        metrics={'code_output': 'accuracy', 'label_output': 'accuracy'}
    )

# Train the model
history = model.fit(
    X_train, 
    {'code_output': y_train_code, 'label_output': y_train_label},
    epochs=200,  # Reduced epochs to minimize resource usage
    batch_size=32,  # Adjusted batch size for better performance
    validation_data=(X_test, {'code_output': y_test_code, 'label_output': y_test_label}),
    callbacks=[early_stopping, lr_scheduler]
)

# Evaluate the model
model.evaluate(X_test, {'code_output': y_test_code, 'label_output': y_test_label}, batch_size=32)

# Predictions and Classification Report
y_pred_code, y_pred_label = model.predict(X_test)

y_pred_code = np.argmax(y_pred_code, axis=1)
y_pred_label = np.argmax(y_pred_label, axis=1)

print("Classification Report for Code:")
print(classification_report(y_test_code, y_pred_code))

print("Classification Report for Label:")
print(classification_report(y_test_label, y_pred_label))

# Make predictions on new text
unstructured_text = """patient name: patricia stith i date of birth: 08/28/1947 nose: mucosa: normal, pink and moist. septum: not markedly deformed. turbinates: normal size and confrontation. polyps: none lips, teeth, gums: normal lips, normal gums, normal dentition. oral mucosa: normal, moist..."""

unstructured_text_clean = clean_text(unstructured_text)
unstructured_sequence = tokenizer.texts_to_sequences([unstructured_text_clean])
unstructured_sequence = pad_sequences(unstructured_sequence, padding='post', maxlen=100)

pred_code, pred_label = model.predict(unstructured_sequence)

pred_code_label = code_encoder.inverse_transform(np.argmax(pred_code, axis=1))
pred_label_label = label_encoder.inverse_transform(np.argmax(pred_label, axis=1))

print(f"Predicted Code: {pred_code_label[0]}")
print(f"Predicted Label: {pred_label_label[0]}")


In [ ]:
unstructured_text = """
"Male with 46, xx karyotype"
"""
unstructured_text_clean = clean_text(unstructured_text)
print(unstructured_text_clean)

unstructured_sequence = tokenizer.texts_to_sequences([unstructured_text_clean])
print(unstructured_sequence)
unstructured_sequence = pad_sequences(unstructured_sequence, padding='post', maxlen=100)
print(unstructured_sequence)

pred_code, pred_label = model.predict(unstructured_sequence)
pred_code_label = code_encoder.inverse_transform(np.argmax(pred_code, axis=1))
pred_label_label = label_encoder.inverse_transform(np.argmax(pred_label, axis=1))

print(f"Predicted Code: {pred_code_label[0]}")
print(f"Predicted Label: {pred_label_label[0]}")


In [ ]:
import pandas as pd
import re
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import classification_report
from sklearn.utils.class_weight import compute_class_weight
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Embedding, LSTM, Dense, Dropout, Bidirectional, BatchNormalization, GlobalMaxPooling1D
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau
from tensorflow.keras import Input
from tensorflow.keras.regularizers import l2

# Check for GPU
print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))

# Load the JSON data into a pandas DataFrame
data = pd.read_json('/kaggle/input/datano/diagnox.json')
df = pd.DataFrame(data)

# Check for None or NaN values
print("Checking for None or NaN values:")
print(df.isna().sum())

# Data Preprocessing and Text Cleaning
def clean_text(text):
    if text is None:
        return ''  # If text is None, return an empty string
    text = re.sub(r'[^a-zA-Z\s]', '', text)  # Remove non-alphanumeric characters
    text = text.lower()  # Convert text to lowercase
    return text

# Fill any NaN or None descriptions with an empty string
df['description'] = df['description'].fillna('')

# Clean the descriptions
df['cleaned_description'] = df['description'].apply(clean_text)

# Tokenization and Sequence Padding
tokenizer = Tokenizer(num_words=10000)  # Using top 10000 words
tokenizer.fit_on_texts(df['cleaned_description'])
X = tokenizer.texts_to_sequences(df['cleaned_description'])
maxlen = 200  # Increase sequence length to 200 to capture more context
X = pad_sequences(X, padding='post', maxlen=maxlen)

# Label Encoding for 'code' and 'label'
code_encoder = LabelEncoder()
df['encoded_code'] = code_encoder.fit_transform(df['code'])

label_encoder = LabelEncoder()
df['encoded_label'] = label_encoder.fit_transform(df['label'])

y_code = df['encoded_code']
y_label = df['encoded_label']

# Train-Test Split
X_train, X_test, y_train_code, y_test_code, y_train_label, y_test_label = train_test_split(
    X, y_code, y_label, test_size=0.2, random_state=42
)

# Compute Class Weights
class_weights_code = compute_class_weight('balanced', classes=np.unique(y_train_code), y=y_train_code)
class_weights_label = compute_class_weight('balanced', classes=np.unique(y_train_label), y=y_train_label)

class_weight_dict_code = {i: class_weights_code[i] for i in range(len(class_weights_code))}
class_weight_dict_label = {i: class_weights_label[i] for i in range(len(class_weights_label))}

# Callbacks and Model Definitions
early_stopping = EarlyStopping(monitor='val_loss', patience=3 ,  restore_best_weights=True)
lr_scheduler = ReduceLROnPlateau(monitor='val_loss', factor=0.5, patience=3, min_lr=1e-6)

# Model Architecture
input_layer = Input(shape=(maxlen,))
embedding_layer = Embedding(input_dim=10000, output_dim=128, input_length=maxlen)(input_layer)
lstm_layer = Bidirectional(LSTM(units=128, return_sequences=True, kernel_regularizer=l2(0.005)))(embedding_layer)
lstm_layer = BatchNormalization()(lstm_layer)
pooling_layer = GlobalMaxPooling1D()(lstm_layer)  # Add a pooling layer to reduce the dimensionality
dropout_layer = Dropout(0.5)(pooling_layer)  # Adjusted dropout rate to avoid overfitting
dense_layer = Dense(64)(dropout_layer)
dense_layer = BatchNormalization()(dense_layer)
dense_layer = tf.keras.layers.ReLU()(dense_layer)  # ReLU for better training dynamics

code_output = Dense(len(code_encoder.classes_), activation='softmax', name='code_output')(dense_layer)
label_output = Dense(len(label_encoder.classes_), activation='softmax', name='label_output')(dense_layer)

model = Model(inputs=input_layer, outputs=[code_output, label_output])

model.summary()

model.compile(optimizer='adam', 
              loss={'code_output': 'categorical_crossentropy', 'label_output': 'categorical_crossentropy'}, 
              metrics={'code_output': 'accuracy', 'label_output': 'accuracy'})

# One-hot encode labels for categorical cross-entropy
y_train_code_onehot = tf.keras.utils.to_categorical(y_train_code, num_classes=len(code_encoder.classes_))
y_test_code_onehot = tf.keras.utils.to_categorical(y_test_code, num_classes=len(code_encoder.classes_))

y_train_label_onehot = tf.keras.utils.to_categorical(y_train_label, num_classes=len(label_encoder.classes_))
y_test_label_onehot = tf.keras.utils.to_categorical(y_test_label, num_classes=len(label_encoder.classes_))

# Custom loop to apply class weights for each output
history = model.fit(X_train, {'code_output': y_train_code_onehot, 'label_output': y_train_label_onehot},
                    epochs=1000, batch_size=32, validation_data=(X_test, {'code_output': y_test_code_onehot, 'label_output': y_test_label_onehot}),
                    callbacks=[early_stopping, lr_scheduler])

# Evaluate the model
model.evaluate(X_test, {'code_output': y_test_code_onehot, 'label_output': y_test_label_onehot}, batch_size=32)

# Classification Report
y_pred_code, y_pred_label = model.predict(X_test)
y_pred_code = np.argmax(y_pred_code, axis=1)
y_pred_label = np.argmax(y_pred_label, axis=1)

print("Classification Report for Code:")
print(classification_report(y_test_code, y_pred_code))

print("Classification Report for Label:")
print(classification_report(y_test_label, y_pred_label))

# Make Predictions on New Unstructured Text
unstructured_text = """patient name: patricia stith i date of birth: 08/28/1947 nose: mucosa: normal, pink and moist. septum: not markedly deformed. turbinates: normal size and confrontation. polyps: none lips, teeth, gums: normal lips, normal gums, normal dentition. oral mucosa: normal, moist..."""
unstructured_text_clean = clean_text(unstructured_text)

unstructured_sequence = tokenizer.texts_to_sequences([unstructured_text_clean])
unstructured_sequence = pad_sequences(unstructured_sequence, padding='post', maxlen=maxlen)

pred_code, pred_label = model.predict(unstructured_sequence)

pred_code_label = code_encoder.inverse_transform(np.argmax(pred_code, axis=1))
pred_label_label = label_encoder.inverse_transform(np.argmax(pred_label, axis=1))

print(f"Predicted Code: {pred_code_label[0]}")
print(f"Predicted Label: {pred_label_label[0]}")


# llama pre-trained model using Health

In [ ]:
import pandas as pd
import json
from datasets import Dataset

# Load your data (assuming it's in JSON format)
with open('/kaggle/input/datano/diagnox.json') as f:
    data = json.load(f)

# Convert the data into a pandas DataFrame
df = pd.DataFrame(data)

# Clean the description text
def clean_text(text):
    text = text.lower()
    text = re.sub(r'[^a-zA-Z\s]', '', text)
    return text

df['cleaned_description'] = df['description'].apply(clean_text)

# Optional: Encoding labels if needed (you may not need to encode if using text-based labels)
from sklearn.preprocessing import LabelEncoder
label_encoder = LabelEncoder()
df['encoded_label'] = label_encoder.fit_transform(df['label'])
df['encoded_code'] = label_encoder.fit_transform(df['code'])

# Prepare input and labels
X = df['cleaned_description'].tolist()
y_code = df['encoded_code'].values
y_label = df['encoded_label'].values

# Convert to Hugging Face Dataset
train_data = Dataset.from_dict({'text': X, 'code': y_code, 'label': y_label})


In [ ]:
! pip install unsloth

In [ ]:
!pip uninstall -y torchvision
!pip install torchvision==0.15.1


In [ ]:
from unsloth.chat_templates import get_chat_template

# Initialize the tokenizer with chat template
tokenizer = get_chat_template(
    tokenizer,
    chat_template = "llama-3.1",  # Use the template matching your model
)

# Formatting function for your dataset
def formatting_prompts_func(examples):
    texts = [f"Description: {text}\nCode: {code}\nLabel: {label}" for text, code, label in zip(examples['text'], examples['code'], examples['label'])]
    return { "text": texts }

# Apply formatting
train_data = train_data.map(formatting_prompts_func, batched=True)

In [ ]:
! pip install unsloth

In [ ]:
!pip install transformers datasets torch

In [2]:
import pandas as pd
import json

# Load JSON data from file
with open("/kaggle/input/datano/diagnox.json", "r") as f:
    data = json.load(f)

# Convert list of dictionaries to a pandas DataFrame
df = pd.DataFrame(data)

# Format the data
formatted_data = [{"text": f"Description: {item['description']} Code: {item['code']}"} for item in data]


print(formatted_data)


[{'text': 'Description: Diabetes mellitus type 2 with complications Code: E1151'}, {'text': 'Description: Diabetes type 2 with circulation disorder Code: E1151'}, {'text': 'Description: Peripheral circulatory disorder associated with type 2 diabetes mellitus Code: E1151'}, {'text': 'Description: Peripheral circulatory disorder associated with type ii diabetes mellitus Code: E1151'}, {'text': 'Description: Peripheral circulatory disorder due to type 2 diabetes mellitus Code: E1151'}, {'text': 'Description: Small vessel disease due to type 2 diabetes mellitus Code: E1151'}, {'text': 'Description: Diabetes type 1 with peripheral vascular disease Code: E1051'}, {'text': 'Description: Diabetes type 1 with small vessel disease Code: E1051'}, {'text': 'Description: Peripheral angiopathy due to type 1 diabetes mellitus Code: E1051'}, {'text': 'Description: Small vessel disease due to type 1 diabetes mellitus Code: E1051'}, {'text': 'Description: Drug induced diabetes with peripheral vascular d

In [ ]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer, Trainer, TrainingArguments
from datasets import Dataset

# Convert the data into a Dataset object
train_dataset = Dataset.from_list(formatted_data)

# Load the pre-trained GPT-2 model and tokenizer
tokenizer = GPT2Tokenizer.from_pretrained("gpt2")
model = GPT2LMHeadModel.from_pretrained("gpt2")

# Add a padding token to the tokenizer (use EOS token as padding token)
tokenizer.pad_token = tokenizer.eos_token

# Tokenize the dataset and prepare the labels for training
def tokenize_function(examples):
    # Tokenize the text and create the labels (shifted by one position)
    encodings = tokenizer(examples['text'], padding="max_length", truncation=True, max_length=256)
    encodings['labels'] = encodings['input_ids'].copy()  # Labels are the same as the input
    return encodings

train_dataset = train_dataset.map(tokenize_function, batched=True)

# Define the training arguments
training_args = TrainingArguments(
    output_dir="./gpt2_diagnosis_model",
    num_train_epochs=3,
    per_device_train_batch_size=2,
    save_steps=10_000,
    save_total_limit=2,
)

# Set up the Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset
)

# Train the model
trainer.train()

# Save the fine-tuned model
trainer.save_model("./gpt2_diagnosis_model")

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

...

Map:   0%|          | 0/62720 [00:00<?, ? examples/s]

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

  ········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [3]:
! pip install datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 8.5 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 11.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 8.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 14.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 36.9 MB/s eta 0:00:0000:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 205.1/205.1 kB 16.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.6/124.6 kB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 319.7/319.7 kB 16.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 241.9/241.9 kB 14.5 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
  Attempting u

In [2]:
import pandas as pd
import numpy as np
import re
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import load_model

# Load the JSON data into a pandas DataFrame
data = pd.read_json('/kaggle/input/datano/diagnox.json')

# Convert JSON data to DataFrame
df = pd.DataFrame(data)

# Define the text cleaning function
def clean_text(text):
    if text is None:
        return ''  # If text is None, return an empty string
    text = re.sub(r'[^a-zA-Z\s]', '', text)  # Remove non-alphanumeric characters
    text = text.lower()  # Convert text to lowercase
    return text

# Fill any NaN or None descriptions with an empty string
df['description'] = df['description'].fillna('')

# Clean the descriptions
df['cleaned_description'] = df['description'].apply(clean_text)

# 1. Refit the Tokenizer
tokenizer = Tokenizer(num_words=10000)
tokenizer.fit_on_texts(df['cleaned_description'])

# 2. Refit the LabelEncoders
code_encoder = LabelEncoder()
df['encoded_code'] = code_encoder.fit_transform(df['code'])

label_encoder = LabelEncoder()
df['encoded_label'] = label_encoder.fit_transform(df['label'])

# Load the trained model
model = load_model('/kaggle/input/model/final_model.h5')

# Input unstructured text
unstructured_text = "Idiopathic aseptic necrosis of"

# Clean the input text
unstructured_text_clean = clean_text(unstructured_text)

# Convert the cleaned text to sequences using the tokenizer
unstructured_sequence = tokenizer.texts_to_sequences([unstructured_text_clean])

# Pad the sequences
unstructured_sequence = pad_sequences(unstructured_sequence, padding='post', maxlen=100)

# Predict the code and label using the model
pred_code, pred_label = model.predict(unstructured_sequence)

# Get the predicted code and label
pred_code_label = code_encoder.inverse_transform(np.argmax(pred_code, axis=1))
pred_label_label = label_encoder.inverse_transform(np.argmax(pred_label, axis=1))

# Get the confidence for the predicted code and label (probability of the predicted class)
pred_code_confidence = np.max(pred_code)
pred_label_confidence = np.max(pred_label)

# Print the predictions along with their confidence
print(f"Predicted Code: {pred_code_label[0]} with confidence {pred_code_confidence:.4f}")
print(f"Predicted Label: {pred_label_label[0]} with confidence {pred_label_confidence:.4f}")


E0000 00:00:1734697560.364305      13 common_lib.cc:798] Could not set metric server port: INVALID_ARGUMENT: Could not find SliceBuilder port 8471 in any of the 0 ports provided in `tpu_process_addresses`="local"
=== Source Location Trace: === 
learning/45eac/tfrc/runtime/common_lib.cc:479
D1220 12:26:00.372556959      13 config.cc:196]                        gRPC EXPERIMENT call_status_override_on_cancellation   OFF (default:OFF)
D1220 12:26:00.372571724      13 config.cc:196]                        gRPC EXPERIMENT call_v3                                OFF (default:OFF)
D1220 12:26:00.372575157      13 config.cc:196]                        gRPC EXPERIMENT canary_client_privacy                  ON  (default:ON)
D1220 12:26:00.372577584      13 config.cc:196]                        gRPC EXPERIMENT capture_base_context                   ON  (default:ON)
D1220 12:26:00.372579911      13 config.cc:196]                        gRPC EXPERIMENT client_idleness                        ON  (defa

NotFoundError: Graph execution error:

Detected at node StatefulPartitionedCall defined at (most recent call last):
  File "/usr/local/lib/python3.10/runpy.py", line 196, in _run_module_as_main

  File "/usr/local/lib/python3.10/runpy.py", line 86, in _run_code

  File "/usr/local/lib/python3.10/site-packages/ipykernel_launcher.py", line 18, in <module>

  File "/usr/local/lib/python3.10/site-packages/traitlets/config/application.py", line 1075, in launch_instance

  File "/usr/local/lib/python3.10/site-packages/ipykernel/kernelapp.py", line 739, in start

  File "/usr/local/lib/python3.10/site-packages/tornado/platform/asyncio.py", line 205, in start

  File "/usr/local/lib/python3.10/asyncio/base_events.py", line 603, in run_forever

  File "/usr/local/lib/python3.10/asyncio/base_events.py", line 1909, in _run_once

  File "/usr/local/lib/python3.10/asyncio/events.py", line 80, in _run

  File "/usr/local/lib/python3.10/site-packages/ipykernel/kernelbase.py", line 545, in dispatch_qu

In [3]:
import tensorflow as tf
print("TensorFlow version:", tf.__version__)
print("Num GPUs Available: ", len(tf.config.experimental.list_physical_devices('GPU')))


TensorFlow version: 2.16.1
Num GPUs Available:  0
